### Reviews about Grab

In this notebook, we are going to perform topic modelling based on sentiments from various review sites. 

In [1]:
# Base
import os, re, string
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
# from wordcloud import WordCloud

# NLTK
import nltk
nltk.download('stopwords')
from nltk.tokenize import sent_tokenize, word_tokenize, RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.metrics.distance import edit_distance
from spellchecker import SpellChecker
from nltk.corpus import stopwords
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.stem.wordnet import WordNetLemmatizer

# Topic Modelling
import pyLDAvis
import pyLDAvis.gensim
import gensim
from gensim import corpora
pyLDAvis.enable_notebook()

[nltk_data] Downloading package stopwords to D:\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


D:\Windows\88B90FF3D0D3454AAACE9B026E2829E3.TMP\Anaconda\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
D:\Windows\88B90FF3D0D3454AAACE9B026E2829E3.TMP\Anaconda\lib\site-packages\scipy\sparse\sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


### Data Preparation

We will first get the relevant files we need and thereafter extract them out into a list of reviews.

In [2]:
# Merge into 

path='.'

filename_sentiment_list=[]

for filename in os.listdir(path):
    if filename.endswith(".csv"):
        # Check what are the files in the folder
        print(os.path.join(path, filename))
        
        #Read the files and put to df
        df = pd.read_csv(filename,encoding = "ISO-8859-1")
        
        #Add it into a list
        try:
            filename_sentiment_list.extend(df['comment'].tolist())
            filename_sentiment_list.extend(df['tweet'].tolist())
            filename_sentiment_list.extend(df['title'].tolist())
        except:
            pass

print(filename_sentiment_list)

.\fb_groups_grab_en.csv
.\gplay_grab_en.csv
.\reddit_grabcar.csv
.\reddit_grabcar_extracted.csv
.\reddit_GrabSG.csv
.\reddit_GrabSG_extracted.csv
.\reddit_grabtaxi.csv
.\reddit_grabtaxi_extracted.csv
.\reddit_grab_driver.csv
.\reddit_grab_driver_extracted.csv
.\reddit_grab_taxi_ride.csv
.\reddit_grab_taxi_ride_extracted.csv
.\reddit_justgrab.csv
.\reddit_justgrab_extracted.csv
.\twitter_GrabSG.csv
.\twitter_grabshare.csv
.\twitter_grabtaxi.csv
.\twitter_grab_driver.csv
.\twitter_grab_taxi_ride.csv
.\twitter_justgrab.csv
.\twitter_str_grabcar_en.csv
.\twitter_str_grabhitch_en.csv
['He sounds a little dodgy.', 'Is dodgy. Report and see what ryde says. I can get it if your bf did not inform it was him coming down but despite it all the responses he gave is just too weird IMHO.', "Why can't ur bf use his acc and book himself?", 'sorry but i dun find anything wrong with his msg to complain', 'To expedite your request., pls indicate in notes that you are booking on behalf.', 'Maybe army regu

In [3]:
filename_sentiment_list[5:7]

['Maybe army regular, talk as though he is in army like that.',
 'I think he is trying to be funny with you.']

### Cleaning

We will also perform cleaning

In [4]:
def clean_list_tokenise(reviews_list):
    # Tokenise the words
    tokenizer = RegexpTokenizer(r'\w+')
    return [tokenizer.tokenize(sentence) for sentence in reviews_list]

def clean_list_lemma(reviews_list):
    # Lemmatization
    lemma = WordNetLemmatizer()
    return [[lemma.lemmatize(word) for word in sentence] for sentence in reviews_list]

def clean_list_stopwords(reviews_list, stop_other=[]):
    def stopword_condition(word):
        word = word.lower()
        
        return word not in stopwords.words('english') \
            and word not in stop_other \
            and word[:5] != 'http' \
            and word[:5] != 'https' \
            and word[:2] != 'RT' \
            and word[0] != '@'
    
    return [[w for w in s if stopword_condition(w)] for s in reviews_list]

In [5]:
sentiment_filtered = clean_list_stopwords(clean_list_tokenise(filename_sentiment_list))
len(sentiment_filtered)

49720

In [6]:
sentiment_filtered_sentences = [' '.join(s) for s in sentiment_filtered]
sentiment_filtered_sentences[:5]

['sounds little dodgy',
 'dodgy Report see ryde says get bf inform coming despite responses gave weird IMHO',
 'ur bf use acc book',
 'sorry dun find anything wrong msg complain',
 'expedite request pls indicate notes booking behalf']

### Segregating by Sentiment

We will segregate the reviews by sentiment. This is achieved by the `analyse_sentiment_vader` function, which uses vader to help us analyse the degree to which the particular review or comment is positive, negative or neutral. It also computes a compound score ranging from -1 to 1 which takes into account all the scores. More reading for the sentiment analysis are available at:

- https://opensourceforu.com/2016/12/analysing-sentiments-nltk/
- http://t-redactyl.io/blog/2017/04/using-vader-to-handle-sentiment-analysis-with-social-media-text.html

In [7]:
def analyse_sentiment_vader(df, col_name):
    sid = SentimentIntensityAnalyzer()
    vader = lambda text: sid.polarity_scores(text)
    
    df['vader'] = df[col_name].apply(vader)
    df = pd.merge(df, df['vader'].apply(pd.Series), left_index=True, right_index=True)
    return df.drop(['vader'], axis=1)

In [8]:
df_sentiment_filtered = pd.DataFrame(sentiment_filtered_sentences, columns=['comment'])
df_sentiment_filtered = analyse_sentiment_vader(df_sentiment_filtered, 'comment')
df_sentiment_filtered.head(10)

comment    neg    neu    pos  \
0                                sounds little dodgy  0.446  0.554  0.000   
1  dodgy Report see ryde says get bf inform comin...  0.123  0.778  0.098   
2                                 ur bf use acc book  0.000  1.000  0.000   
3         sorry dun find anything wrong msg complain  0.633  0.367  0.000   
4  expedite request pls indicate notes booking be...  0.000  0.822  0.178   
5           Maybe army regular talk though army like  0.000  0.706  0.294   
6                                 think trying funny  0.000  0.408  0.592   
7                                Born cheap much sex  0.000  1.000  0.000   
8                                  mother must whore  0.683  0.317  0.000   
9  0330am booking u slept U must really2 tired fu...  0.220  0.530  0.250   

   compound  
0   -0.1548  
1   -0.0982  
2    0.0000  
3   -0.7096  
4    0.0772  
5    0.3612  
6    0.4404  
7    0.0000  
8   -0.6486  
9    0.1027

In [9]:
df_sentiment_filtered.tail(10)

comment    neg    neu    pos  \
49710  need worry grab n uber around taxi less picky ...  0.102  0.810  0.088   
49711  ComfortDelgro one fav cab service im rush call...  0.000  0.765  0.235   
49712  Comfort Delgro also got phone app works simila...  0.000  0.762  0.238   
49713                                im sure option pick  0.000  0.566  0.434   
49714         deleted 0 6431 pastebin com FcrFs94k 97666  0.000  1.000  0.000   
49715  support sg grab com go Grab app help centre re...  0.000  0.671  0.329   
49716                               complained shit Grab  0.863  0.137  0.000   
49717                                    show booking id  0.000  1.000  0.000   
49718  kindness monetary incentive see driver deliver...  0.111  0.536  0.353   
49719                          grab hitch driver spotted  0.000  1.000  0.000   

       compound  
49710   -0.1027  
49711    0.5106  
49712    0.7579  
49713    0.3182  
49714    0.0000  
49715    0.6597  
49716   -0.7430  
49717    0.0000  
49718    0.9643  
49719    0.0000

In [10]:
pos_list = list(df_sentiment_filtered[df_sentiment_filtered['compound'] >= 0]['comment'])
neg_list = list(df_sentiment_filtered[df_sentiment_filtered['compound'] < 0]['comment'])

len(pos_list), len(neg_list)

(38954, 10766)

In [11]:
pos_list_clean = clean_list_lemma(clean_list_tokenise(pos_list))
neg_list_clean = clean_list_lemma(clean_list_tokenise(neg_list))

In [12]:
len(pos_list_clean), len(neg_list_clean)

(38954, 10766)

Ignore code below

### Topic Modelling (Negative)

In [13]:
neg_dict = corpora.Dictionary(neg_list_clean)
doc_term_matrix = [neg_dict.doc2bow(doc) for doc in neg_list_clean]

print(doc_term_matrix[0:10])

[[(0, 1), (1, 1), (2, 1)], [(0, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1), (11, 1), (12, 1), (13, 1), (14, 1), (15, 1)], [(16, 1), (17, 1), (18, 1), (19, 1), (20, 1), (21, 1), (22, 1)], [(23, 1), (24, 1), (25, 1)], [(26, 1), (27, 1)], [(27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 2), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1)], [(30, 1), (32, 1), (34, 1), (38, 1), (39, 1), (40, 1)], [(14, 1), (16, 1), (22, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1), (54, 1), (55, 1), (56, 1), (57, 1)], [(9, 1), (12, 1), (13, 1), (27, 2), (32, 1), (52, 1), (58, 1), (59, 1), (60, 1), (61, 2), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 1), (68, 1), (69, 1), (70, 2), (71, 1), (72, 2), (73, 1), (74, 1), (75, 2), (76, 1), (77, 1), (78, 1), (79, 1), (80, 1), (81, 2), (82, 1), (83, 1), (84, 1), (85, 2), (86, 1), (87, 2), (88, 1), (89, 1), (90, 1), (91, 1), (92, 1), (93, 2)], [(17, 2), (51, 1), (6

In [14]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

# Running and Trainign LDA model on the document term matrix.
#doc_term_matrix = frequency of terms of all documents
#dictionary = all unique terms
ldamodel = Lda(doc_term_matrix, num_topics=5, id2word=neg_dict, passes=50)

In [15]:
print(ldamodel.print_topics(num_topics=5, num_words=5))

[(0, '0.017*"driver" + 0.012*"grab" + 0.012*"Grab" + 0.012*"taxi" + 0.010*"uber"'), (1, '0.029*"Grab" + 0.023*"Uber" + 0.012*"service" + 0.009*"grab" + 0.008*"company"'), (2, '0.043*"app" + 0.017*"grab" + 0.016*"use" + 0.013*"time" + 0.013*"update"'), (3, '0.019*"ð" + 0.008*"open" + 0.007*"terrible" + 0.007*"version" + 0.006*"com"'), (4, '0.046*"driver" + 0.020*"time" + 0.014*"ride" + 0.014*"cancel" + 0.012*"get"')]


In [16]:
pyLDAvis.gensim.prepare(ldamodel, doc_term_matrix, neg_dict)

D:\Windows\88B90FF3D0D3454AAACE9B026E2829E3.TMP\Anaconda\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=True'.

To retain the current behavior and silence the warning, pass sort=False

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4      0.144338  0.013671       1        1  33.221348
2      0.078307 -0.254152       2        1  21.525511
0      0.089649  0.165429       3        1  20.798101
1      0.033136  0.076668       4        1  16.005699
3     -0.345430 -0.001615       5        1   8.449348, topic_info=      Category         Freq          Term        Total  loglift  logprob
term                                                                    
68     Default  2555.000000        driver  2555.000000  30.0000  30.0000
62     Default  1741.000000           app  1741.000000  29.0000  29.0000
648    Default  1399.000000          Grab  1399.000000  28.0000  28.0000
410    Default   961.000000          Uber   961.000000  27.0000  27.0000
148    Default   617.000000        cancel   617.000000  26.0000  26.0000
27     Default  1353.000000          time  1353.000000  25.0000  25.0000
1570   Default   376.000000        update   376.000000  24.0000  24.0000
451    Default   524.000000       booking   524.000000  23.0000  23.0000
5524   Default   222.000000             ð   222.000000  22.0000  22.0000
2906   Default   356.000000          code   356.000000  21.0000  21.0000
139    Default   663.000000           use   663.000000  20.0000  20.0000
147    Default   541.000000        always   541.000000  19.0000  19.0000
52     Default   769.000000          ride   769.000000  18.0000  18.0000
337    Default   364.000000          suck   364.000000  17.0000  17.0000
551    Default   263.000000          cant   263.000000  16.0000  16.0000
158    Default   312.000000       account   312.000000  15.0000  15.0000
234    Default   337.000000          pick   337.000000  14.0000  14.0000
73     Default  1252.000000          grab  1252.000000  13.0000  13.0000
3411   Default   218.000000           fix   218.000000  12.0000  12.0000
1268   Default   218.000000         error   218.000000  11.0000  11.0000
78     Default   478.000000       problem   478.000000  10.0000  10.0000
45     Default   292.000000       company   292.000000   9.0000   9.0000
365    Default   576.000000          taxi   576.000000   8.0000   8.0000
524    Default   708.000000           bad   708.000000   7.0000   7.0000
1233   Default   510.000000      location   510.000000   6.0000   6.0000
794    Default   429.000000          uber   429.000000   5.0000   5.0000
164    Default   267.000000        people   267.000000   4.0000   4.0000
103    Default   354.000000          fare   354.000000   3.0000   3.0000
942    Default   252.000000         phone   252.000000   2.0000   2.0000
379    Default   281.000000        minute   281.000000   1.0000   1.0000
...        ...          ...           ...          ...      ...      ...
3782    Topic5    24.817678          game    25.512392   2.4435  -6.1453
597     Topic5    23.218935           Pay    23.875298   2.4432  -6.2119
2046    Topic5    24.006269   information    24.697435   2.4427  -6.1786
10453   Topic5    20.077263        jailed    20.724596   2.4393  -6.3573
3529    Topic5    20.194036  Singaporeans    20.857363   2.4388  -6.3515
13554   Topic5    19.298933          apos    19.947105   2.4380  -6.3968
5717    Topic5    19.327240           APP    19.976652   2.4380  -6.3954
6056    Topic5    18.995174            na    19.643038   2.4375  -6.4127
6263    Topic5    18.961056          knew    19.636518   2.4361  -6.4145
961     Topic5    18.631111           bye    19.299562   2.4358  -6.4320
7786    Topic5    19.046806         Seems    19.731358   2.4358  -6.4100
4768    Topic5    18.463783       ability    19.152653   2.4345  -6.4411
6717    Topic5    16.977791          2018    17.639326   2.4329  -6.5250
5732    Topic5    16.071501            ng    16.719900   2.4315  -6.5798
5643    Topic5    16.394073          Went    17.058657   2.4313  -6.5600
10793   Topic5    25.188484            ST    27.074347   2.3989  -6.1305
11

# Topic Modelling (Positive)

In [17]:
pos_dict = corpora.Dictionary(pos_list_clean)
doc_term_matrix = [neg_dict.doc2bow(doc) for doc in pos_list_clean]

print(doc_term_matrix[0:10])

[[(5, 1), (139, 1), (190, 1), (554, 1), (3277, 1)], [(364, 1), (451, 1), (725, 1), (736, 1), (949, 1), (2745, 1)], [(304, 1), (392, 1), (600, 1), (611, 2), (711, 1), (1851, 1)], [(405, 1), (664, 1), (5458, 1)], [(64, 1), (202, 1), (10478, 1)], [(24, 1), (88, 1), (360, 1), (451, 1), (554, 1), (1598, 1), (8716, 1), (9094, 1), (11536, 1)], [(7399, 1), (8707, 1)], [(32, 1), (34, 1), (48, 1), (88, 1), (360, 1), (680, 1), (1602, 1)], [(30, 1), (31, 1), (32, 1), (75, 1), (2656, 1), (6563, 1)], [(31, 1), (48, 1), (139, 1), (240, 2), (1115, 1), (5543, 1)]]


In [18]:
# Creating the object for LDA model using gensim library
Lda = gensim.models.ldamodel.LdaModel

# Running and Trainign LDA model on the document term matrix.
#doc_term_matrix = frequency of terms of all documents
#dictionary = all unique terms
ldamodel = Lda(doc_term_matrix, num_topics=5, id2word=pos_dict, passes=50)

In [19]:
pyLDAvis.gensim.prepare(ldamodel, doc_term_matrix, pos_dict)

D:\Windows\88B90FF3D0D3454AAACE9B026E2829E3.TMP\Anaconda\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=True'.

To retain the current behavior and silence the warning, pass sort=False

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.128093  0.117247       1        1  28.248882
2     -0.180038 -0.029635       2        1  23.613523
0     -0.183819 -0.058851       3        1  23.291702
3      0.235654 -0.302104       4        1  12.892985
4      0.256297  0.273344       5        1  11.952906, topic_info=     Category         Freq        Term        Total  loglift  logprob
term                                                                 
1651  Default  2689.000000      venson  2689.000000  30.0000  30.0000
62    Default  3952.000000    speaking  3952.000000  29.0000  29.0000
648   Default  3130.000000     rdyepay  3130.000000  28.0000  28.0000
410   Default  2168.000000        many  2168.000000  27.0000  27.0000
390   Default  2466.000000         fee  2466.000000  26.0000  26.0000
5524  Default   939.000000   protected   939.000000  25.0000  25.0000
116   Default  1505.000000         job  1505.000000  24.0000  24.0000
392   Default  1852.000000       least  1852.000000  23.0000  23.0000
27    Default  2072.000000           U  2072.000000  22.0000  22.0000
365   Default  1549.000000       twice  1549.000000  21.0000  21.0000
68    Default  3614.000000      choose  3614.000000  20.0000  20.0000
8771  Default   690.000000      circle   690.000000  19.0000  19.0000
103   Default   620.000000        till   620.000000  18.0000  18.0000
794   Default   858.000000         ½On   858.000000  17.0000  17.0000
73    Default  2467.000000      option  2467.000000  16.0000  16.0000
202   Default   821.000000   important   821.000000  15.0000  15.0000
375   Default   937.000000        free   937.000000  14.0000  14.0000
3917  Default   541.000000     Partime   541.000000  13.0000  13.0000
2906  Default   873.000000     Branded   873.000000  12.0000  12.0000
88    Default   750.000000      petrol   750.000000  11.0000  11.0000
405   Default   728.000000        came   728.000000  10.0000  10.0000
2191  Default   482.000000       Leong   482.000000   9.0000   9.0000
504   Default   451.000000        goon   451.000000   8.0000   8.0000
1512  Default   758.000000    provider   758.000000   7.0000   7.0000
139   Default  1890.000000     pancake  1890.000000   6.0000   6.0000
1224  Default   429.000000       motto   429.000000   5.0000   5.0000
498   Default  1186.000000        link  1186.000000   4.0000   4.0000
4022  Default   432.000000      EXCEPT   432.000000   3.0000   3.0000
551   Default   406.000000     account   406.000000   2.0000   2.0000
52    Default  1554.000000         got  1554.000000   1.0000   1.0000
...       ...          ...         ...          ...      ...      ...
5482   Topic5   264.130920      Deduct   264.686462   2.1221  -4.7844
1173   Topic5   253.253296   everytime   253.807968   2.1220  -4.8264
3600   Topic5   240.640335  completing   241.193237   2.1219  -4.8775
1213   Topic5   230.824570      person   231.388885   2.1218  -4.9192
1751   Topic5   180.329391          23   180.892044   2.1211  -5.1660
3847   Topic5   166.948959       Vezel   167.506134   2.1209  -5.2431
5677   Topic5   156.063782       GIANT   156.611984   2.1207  -5.3106
1703   Topic5   158.899033        body   159.462570   2.1207  -5.2925
5568   Topic5   142.541138      CHANCE   143.114700   2.1202  -5.4012
2317   Topic5   138.649933     Without   139.209641   2.1202  -5.4289
1085   Topic5   138.367752      workin   138.930008   2.1201  -5.4309
1624   Topic5   147.113785      noodle   147.781311   2.1197  -5.3696
627    Topic5   126.099525        chio   126.685577   2.1196  -5.5237
3713   Topic5   116.202621  elsewhereï   116.756371   2.1194  -5.6055
3420   Topic5   112.857391   efficient   113.416168   2.1193  -5.6347
5375   Topic5   113.198997   reputable   113.771606   2.1192  -5.6317
5891   Topic5   101.218346        obey   101.773468   2.1187  -5.7435
5671   Topic5    99.717026   langchiow   100.289192   2.1185  -5.7585
5508   To